# 1: Upload data
# 2: Create documents

In [480]:
import csv
import pandas as pd
import nltk 
from nltk.corpus import stopwords
from nltk.stem import PorterStemmer
from nltk import word_tokenize
import string
from nltk.tokenize import RegexpTokenizer
import json
import math

In [481]:
#read csv as data frame with pandas
df = pd.read_csv("/Users/milpro/Desktop/Universita/ADM_Aris/HW3/Airbnb_Texas_Rentals.csv")

#remove \\n new line from the description
df = df.replace(r'\\n', " ", regex = True)

#make the df as list
df1 = df.values.tolist()


In [482]:
#create a tsv file with \t tab space for each row from the df1 list
for row in df1:
    with open("/Users/milpro/Desktop/Universita/ADM_Aris/HW3/doc_tsv/doc_" +str(df1.index(row))+ ".tsv", 'w', newline='',encoding='utf8') as f_output:
        tsv_output = csv.writer(f_output, delimiter='\t',)
        tsv_output.writerow(row[1:]) #remove first row with names

In [483]:
len(df) # the number of the documents

18259

In [484]:
df1

[[1,
  '$27',
  '2',
  'Humble',
  'May 2016',
  'Welcome to stay in private room with queen bed and detached private bathroom on the second floor. Another private bedroom with sofa bed is available for additional guests. 10$ for an additional guest. 10min from IAH airport Airport pick-up/drop off is available for $10/trip.',
  30.0201379199512,
  -95.29399600425128,
  '2 Private rooms/bathroom 10min from IAH airport',
  'https://www.airbnb.com/rooms/18520444?location=Cleveland%2C%20TX'],
 [2,
  '$149',
  '4',
  'San Antonio',
  'November 2010',
  'Stylish, fully remodeled home in upscale NW – Alamo Heights Area.   Amazing location - House conveniently located in quiet street, with beautiful seasoned trees, prestigious neighborhood and very close to the airport, 281, 410 loop and down-town area.   Featuring an open floor plan, original hardwood floors, 3 bedrooms, 3 FULL bathrooms + an independent garden-TV room which can sleep 2 more  European inspired kitchen and “top of the line” de

In [485]:
#remove the index from df1
for i in df1:
    i.remove(i[0])

In [486]:
df1 #df1 without the index

[['$27',
  '2',
  'Humble',
  'May 2016',
  'Welcome to stay in private room with queen bed and detached private bathroom on the second floor. Another private bedroom with sofa bed is available for additional guests. 10$ for an additional guest. 10min from IAH airport Airport pick-up/drop off is available for $10/trip.',
  30.0201379199512,
  -95.29399600425128,
  '2 Private rooms/bathroom 10min from IAH airport',
  'https://www.airbnb.com/rooms/18520444?location=Cleveland%2C%20TX'],
 ['$149',
  '4',
  'San Antonio',
  'November 2010',
  'Stylish, fully remodeled home in upscale NW – Alamo Heights Area.   Amazing location - House conveniently located in quiet street, with beautiful seasoned trees, prestigious neighborhood and very close to the airport, 281, 410 loop and down-town area.   Featuring an open floor plan, original hardwood floors, 3 bedrooms, 3 FULL bathrooms + an independent garden-TV room which can sleep 2 more  European inspired kitchen and “top of the line” decor. Drive

In [487]:
#download the stop words
nltk.download("stopwords")

[nltk_data] Downloading package stopwords to
[nltk_data]     /Users/milpro/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


True

In [488]:
stopwords = stopwords.words('english') # get english stop words

#we tokenize except for the symbol $ that remains with the value
tokenizer = RegexpTokenizer("[\w'\$]+")

#stemming
st = PorterStemmer()

In [489]:
#tokenize description and title
df.description = df.description.apply(str).apply(tokenizer.tokenize)
df.title = df.title.apply(str).apply(tokenizer.tokenize)

#remove stop word and punctuation from description and title
df.description = df.description.apply(lambda x : [item for item in x if item not in stopwords])
df.title = df.title.apply(lambda x : [item for item in x if item not in stopwords])

#remove stemmings from descr and title
df.description = df.description.apply(lambda x : [st.stem(y) for y in x])
df.title = df.title.apply(lambda x : [st.stem(y) for y in x])

In [490]:
df.head() #now we have titles and descriptions cleaned

Unnamed: 0 average_rate_per_night bedrooms_count         city  \
0           1                    $27              2       Humble   
1           2                   $149              4  San Antonio   
2           3                    $59              1      Houston   
3           4                    $60              1        Bryan   
4           5                    $75              2   Fort Worth   

  date_of_listing                                        description  \
0        May 2016  [welcom, stay, privat, room, queen, bed, detac...   
1   November 2010  [stylish, fulli, remodel, home, upscal, NW, al...   
2    January 2017  ['river, hous, island, close, city', A, well, ...   
3   February 2016  [privat, bedroom, cute, littl, home, situat, c...   
4   February 2017  [welcom, origin, 1920', home, We, recent, purc...   

    latitude  longitude                                             title  \
0  30.020138 -95.293996  [2, privat, room, bathroom, 10min, iah, airport]   
1  29.503068 -98.447688     [uniqu, locat, alamo, height, design, inspir]   
2  29.829352 -95.081549                         [river, hous, near, citi]   
3  30.637304 -96.337846                      [privat, room, close, campu]   
4  32.747097 -97.286434                                      [the, porch]   

                                                 url  
0  https://www.airbnb.com/rooms/18520444?location...  
1  https://www.airbnb.com/rooms/17481455?location...  
2  https://www.airbnb.com/rooms/16926307?location...  
3  https://www.airbnb.com/rooms/11839729?location...  
4  https://www.airbnb.com/rooms/17325114?location...

# 3: SEARCH ENGINE
## 3.1 Conjunctive query

### 3.1.1 Create your index!

In [491]:
#create the list of all the words
voc = []

for i in list(df.description):
    for j in i:
        voc.append(j)
for i in list(df.title):
    for j in i:
        voc.append(j)
        
voc = set(voc) #convert the list to a set of distinct words

In [492]:
voc

{'rural',
 'OP',
 'greenbelt',
 'oli',
 'burrito',
 'T2',
 'drivetim',
 'surfsidetx',
 '1103',
 '810',
 'lgbtq',
 'haul',
 'hassl',
 'enclos',
 'consciou',
 'robber',
 'higway',
 'baldi',
 'ceiba',
 'headach',
 'septiembr',
 'shallow',
 'rita',
 'eighti',
 '40m',
 'artist',
 'viewpoint',
 'quaintli',
 '1996',
 'known',
 "ron'",
 'angler',
 'jungl',
 'secretli',
 'De',
 'shuttl',
 'moo',
 'express',
 'bien',
 'canin',
 'elmtopia',
 'bit',
 'bluegil',
 'promptli',
 'tenemo',
 'intv',
 'coyot',
 'frío',
 'azalea',
 'bradi',
 'dilbeck',
 'gallaria',
 'walker',
 'bar',
 'comun',
 'coveni',
 'care',
 'farimount',
 'sophi',
 'strand',
 'AQ',
 'eiffel',
 'gruen',
 'swimmimg',
 'activit',
 '252',
 'lewi',
 '1512',
 'marion',
 'gregori',
 'nikken',
 'freestand',
 'windi',
 'citronella',
 'winteri',
 'dgh',
 'ibm',
 'butcher',
 'dia',
 'below',
 'bound',
 'ing',
 'cypress',
 'hopdoddi',
 'n',
 'En',
 '4013',
 'lemon',
 'endear',
 '574',
 'yet',
 'displac',
 '83',
 'a13',
 'until',
 'fill',
 'gift

In [493]:
num = list(voc) #make voc as list
vocabulary = {} #create empty dictionary

for i in num:
    vocabulary.update({num.index(i):i}) # get a key for each value of voc

In [494]:
vocabulary #we associate a number to each word

{0: 'rural',
 1: 'OP',
 2: 'greenbelt',
 3: 'oli',
 4: 'burrito',
 5: 'T2',
 6: 'drivetim',
 7: 'surfsidetx',
 8: '1103',
 9: '810',
 10: 'lgbtq',
 11: 'haul',
 12: 'hassl',
 13: 'enclos',
 14: 'consciou',
 15: 'robber',
 16: 'higway',
 17: 'baldi',
 18: 'ceiba',
 19: 'headach',
 20: 'septiembr',
 21: 'shallow',
 22: 'rita',
 23: 'eighti',
 24: '40m',
 25: 'artist',
 26: 'viewpoint',
 27: 'quaintli',
 28: '1996',
 29: 'known',
 30: "ron'",
 31: 'angler',
 32: 'jungl',
 33: 'secretli',
 34: 'De',
 35: 'shuttl',
 36: 'moo',
 37: 'express',
 38: 'bien',
 39: 'canin',
 40: 'elmtopia',
 41: 'bit',
 42: 'bluegil',
 43: 'promptli',
 44: 'tenemo',
 45: 'intv',
 46: 'coyot',
 47: 'frío',
 48: 'azalea',
 49: 'bradi',
 50: 'dilbeck',
 51: 'gallaria',
 52: 'walker',
 53: 'bar',
 54: 'comun',
 55: 'coveni',
 56: 'care',
 57: 'farimount',
 58: 'sophi',
 59: 'strand',
 60: 'AQ',
 61: 'eiffel',
 62: 'gruen',
 63: 'swimmimg',
 64: 'activit',
 65: '252',
 66: 'lewi',
 67: '1512',
 68: 'marion',
 69: 'gr

It can be observed the presence of some words in oriental characters (logograms). We decide to not remove them because since we are representing real data, it can not be excluded that the query or the websites are in another language.
We will show later for the word number 152 - 别墅二层独立房间 that it is included in a real web site.

In [495]:
#we save the vocabulary as json file
with open("/Users/milpro/Desktop/Universita/ADM_Aris/HW3/vocabulary.json", "w", encoding = "utf8") as myfile:
    myfile.write(json.dumps(vocabulary))

In [496]:
#create dict from df that assign for each rows (doc) all the words in
newdict = {}
for index, row in df.iterrows():
    newdict["doc_" + str(index)] = list(row["description"]) + list(row["title"])

In [497]:
newdict

{'doc_0': ['welcom',
  'stay',
  'privat',
  'room',
  'queen',
  'bed',
  'detach',
  'privat',
  'bathroom',
  'second',
  'floor',
  'anoth',
  'privat',
  'bedroom',
  'sofa',
  'bed',
  'avail',
  'addit',
  'guest',
  '10$',
  'addit',
  'guest',
  '10min',
  'iah',
  'airport',
  'airport',
  'pick',
  'drop',
  'avail',
  '$10',
  'trip',
  '2',
  'privat',
  'room',
  'bathroom',
  '10min',
  'iah',
  'airport'],
 'doc_1': ['stylish',
  'fulli',
  'remodel',
  'home',
  'upscal',
  'NW',
  'alamo',
  'height',
  'area',
  'amaz',
  'locat',
  'hous',
  'conveni',
  'locat',
  'quiet',
  'street',
  'beauti',
  'season',
  'tree',
  'prestigi',
  'neighborhood',
  'close',
  'airport',
  '281',
  '410',
  'loop',
  'town',
  'area',
  'featur',
  'open',
  'floor',
  'plan',
  'origin',
  'hardwood',
  'floor',
  '3',
  'bedroom',
  '3',
  'full',
  'bathroom',
  'independ',
  'garden',
  'TV',
  'room',
  'sleep',
  '2',
  'european',
  'inspir',
  'kitchen',
  'top',
  'line'

In [498]:
with open("index.json", "w", encoding = "utf8") as myfile:#write normal index to json
    myfile.write(json.dumps(newdict))

In [499]:
#create inverted index called inverse

inverse = dict() 
for key in newdict: 
    # Go through the list that is saved in the dict:
    for item in set(newdict[key]):
        # Check if in the inverted dict the key exists
        if item not in inverse: 
            # If not create a new list
            inverse[item] = [key] 
        else: 
            inverse[item].append(key) 


In [500]:
# change the keys of inverse with the keys of vocabulary
for i in vocabulary:
    inverse[i] = inverse[vocabulary[i]]
    del inverse[vocabulary[i]]

In [501]:
inverse

{0: ['doc_234',
  'doc_462',
  'doc_883',
  'doc_1022',
  'doc_1541',
  'doc_1548',
  'doc_1910',
  'doc_1991',
  'doc_2120',
  'doc_2430',
  'doc_2924',
  'doc_3038',
  'doc_3282',
  'doc_3299',
  'doc_3365',
  'doc_3911',
  'doc_4043',
  'doc_4178',
  'doc_4620',
  'doc_4718',
  'doc_4877',
  'doc_5014',
  'doc_5113',
  'doc_5878',
  'doc_6380',
  'doc_6426',
  'doc_6519',
  'doc_6637',
  'doc_6984',
  'doc_7684',
  'doc_8122',
  'doc_8123',
  'doc_8196',
  'doc_8220',
  'doc_8318',
  'doc_8347',
  'doc_9047',
  'doc_9346',
  'doc_9452',
  'doc_9508',
  'doc_9567',
  'doc_9662',
  'doc_9743',
  'doc_10145',
  'doc_10200',
  'doc_11485',
  'doc_11520',
  'doc_11612',
  'doc_11663',
  'doc_11798',
  'doc_11802',
  'doc_12173',
  'doc_12298',
  'doc_12502',
  'doc_12710',
  'doc_12761',
  'doc_13279',
  'doc_13340',
  'doc_13692',
  'doc_13969',
  'doc_14154',
  'doc_14199',
  'doc_14221',
  'doc_14690',
  'doc_14704',
  'doc_14918',
  'doc_14923',
  'doc_15020',
  'doc_15479',
  'doc_1

In [502]:
#save inverted index as json
with open("/Users/milpro/Desktop/Universita/ADM_Aris/HW3/inverted_index.json", "w", encoding = "utf8") as myfile:
    myfile.write(json.dumps(inverse))

### 3.1.2 Execute the query

In [503]:
#define a function for tokenizer, stemming, remove stop words and punctuation

def clean(doc):
    tokenizer = RegexpTokenizer("[\w'\$]+") #we don't want to split the dollar $ from his price
    doc = tokenizer.tokenize(doc) #tokenize the query for stop word and punctuation
    doc = [t for t in doc if t not in stopwords] #remove stopword
    doc = [st.stem(word) for word in doc] #stemming
    
    return doc

In [504]:
#we create a function for the Search Engine 1

def make_clickable(val): #we will use this to make the urls in output clickable
        # target _blank to open new window
        return '<a target="_blank" href="{}">{}</a>'.format(val, val)

vocabulary = json.loads(open("/Users/milpro/Desktop/Universita/ADM_Aris/HW3/vocabulary.json").read())
vocabulary = {k:v for v,k in vocabulary.items()} #change key as value and viceversa 

def searchEngine_1():
    query = input("Insert your query: ") #user input
    query = clean(query) #tokenizing, stemming, removing stop words and punctuation
    
    inverted_index = json.loads(open("/Users/milpro/Desktop/Universita/ADM_Aris/HW3/inverted_index.json").read())


    for i in set(query):
        if i in vocabulary:
            query.remove(i)
            query.append(vocabulary[i])
        else:
            query.remove(i)
    
    docs = []
    query = set(query)
    
    try:
        for i in query:
            docs.append(set(inverted_index[i]))

    
        docs = set.intersection(*docs)

    except: #make a print of exception "result for your query doesn't exist"

        return print("Result for your query doesn't exist.") #it stops the function if there aren't match 

    results = []
    for file in docs:
        opentsv = open("doc_tsv/" + file + ".tsv", "r", encoding="utf8")
        lines = opentsv.readlines()
        for x in lines:
            results.append([x.split('\t')[7], x.split('\t')[4], x.split('\t')[2], x.split('\t')[8]])
        opentsv.close()

    result = pd.DataFrame(results, columns = ['Title', 'Description', 'City', 'URL'])
    result.Title = result.Title.str.replace('$', '$\$$') #escape the problem with latex codification
    result.Description = result.Description.str.replace('$', '$\$$') #escape the problem with latex codification

    result.style.set_properties(*{'text-align': 'center'})
    
    return result.style.format({'URL': make_clickable}) #make_clickable function

In [505]:
# Let's try "PERGOLA:
searchEngine_1()

Insert your query: pergola


In [506]:
# As we have already said at the beginning, our query with no english words can produces a result.
# es 别墅二层独立房间 as input
searchEngine_1()

Insert your query: 别墅二层独立房间


In [507]:
# check for a non-existent word as "abcdefg"
searchEngine_1()

Insert your query: abcd
Result for your query doesn't exist.


## 3.2 Conjunctive query & Ranking score

### 3.2.1 Inverted index

In [508]:
corpus = json.loads(open('index.json').read())
inverted_index = json.loads(open('inverted_index.json').read())
vocab = json.loads(open('vocabulary.json').read())

In [509]:
vocablist = [x for x in vocabulary.keys()] #list of words


What we need now is to calculate che IDF and TF - IDF, according to the formulas: 
- $TF = \frac{N_{(x,y)}}{N_{(*,y)}}$
- $IDF = log[1 + (\frac{D}{D_x})]$ <fr>

Where:
- $N_{(x,y)}$ is the number of times that the word $X$ is in the document $D_y$;
- $N_{(*,y)}$ is the total number of the words in the document;
- $D$ is the total number of documents;
- $D_x$ is the number of documents in which the word $X$ appears at least once.

In [510]:
# calculate the IDF

idf = {}
for term in inverted_index:
    term1 = vocab[term]
    idf[term] = math.log(1+(len(corpus)/len(term1)))
with open("idf_index.json", "w", encoding = "utf8") as myfile:
    myfile.write(json.dumps(inverted_index))

In [511]:
#calculate the TF - IDF

for term in inverted_index:
    term1 = vocab[term]
    for doc in inverted_index[term]:
        count = (corpus[doc].count(term1)/len(corpus[doc]))*idf[term]
        inverted_index[term][inverted_index[term].index(doc)]=(doc,count)
        
with open("tfidf_index.json", "w", encoding = "utf8") as myfile:
    myfile.write(json.dumps(inverted_index))
    

In [512]:
inverted_index

{'0': [('doc_234', 0.13903812331822935),
  ('doc_462', 0.2929731884205547),
  ('doc_883', 0.12817576993399268),
  ('doc_1022', 0.24858331138713732),
  ('doc_1541', 0.1608480250152065),
  ('doc_1548', 0.2929731884205547),
  ('doc_1910', 0.24858331138713732),
  ('doc_1991', 0.15775479376491408),
  ('doc_2120', 0.16406498551551063),
  ('doc_2430', 0.21033972501988543),
  ('doc_2924', 0.10127468241698187),
  ('doc_3038', 0.14143533234095745),
  ('doc_3282', 0.25635153986798537),
  ('doc_3299', 0.24858331138713732),
  ('doc_3365', 0.25240767002386255),
  ('doc_3911', 0.26462094437985584),
  ('doc_4043', 0.1608480250152065),
  ('doc_4178', 0.21587498094146135),
  ('doc_4620', 0.14648659421027735),
  ('doc_4718', 0.11237327775034975),
  ('doc_4877', 0.09650881500912391),
  ('doc_5014', 0.24858331138713732),
  ('doc_5113', 0.22786803543820922),
  ('doc_5878', 0.12620383501193128),
  ('doc_6380', 0.2689589926483781),
  ('doc_6426', 0.26042061192938193),
  ('doc_6519', 0.13903812331822935),
  ('

### 3.2.2 Execute the query - Cosine Similarity

In [513]:
#it prints the top k results according to the cosine similarity

def searchEngine_2():
    query = input("Insert your query: ")
    k = int(input("How many results do you want to see? "))
    error = []

    query = clean(query)


    for i in query:
        if i in vocabulary:
            query[query.index(i)] = vocabulary[i] #replacing word with id in the query
        else:
            error.append(i) #if is not in vocabulary we append in error
            
    if error != []: #if error not empty
        return print('there are no results that match your search criteria: '+', '.join(error))
    else: #else do the search engine 
        query_tfidf = {}

        for i in query:
            query_tfidf[i] = (query.count(i)/len(query))*(idf[i]) #calculate tf-idf of the words in query

        result_docs = []

        for i in query:
            docs = []
            for j in inverted_index[i]: #access to the number of the query in inverted_index
                docs.append(j[0])  #append the doc without tfidf in docs
            result_docs.append(set(docs)) # distinct documents

        result_docs = list(set.intersection(*result_docs)) #intersection of the documents 

        docsidf = {} 
        for i in query:
            #taking the whole tuple and not single doc
            docsidf[i] = [list(item) for item in inverted_index[i] if item[0] in result_docs]
            
        #product = 0
        docs_norm = {}
        dotproducts = {}

        for name in result_docs: #for each doc in result_docs
            product = 0
            dotproducts[name] = 0
            docs_norm[name] = 0
            for term in query: #for each word in query
                #dotproducts[name] = 0
                # it take the tf-idf score from docsidf at key equal term for the document name 
                idf1 = [x[1] for x in docsidf[term] if x[0] == name]
                product += idf1[0] 
                docs_norm[name] += product**2    
                #make the product of the tfidf between query and doc, and sum the products for each word
                dotproducts[name] += query_tfidf[term]*idf1[0] 
            docs_norm[name] = math.sqrt(docs_norm[name]) 

        query_norm = 0
        for x in query_tfidf:
            query_norm += query_tfidf[x]
        dot_product = 0

        cosine_similarity = {}

        for product in dotproducts:
            cosine_similarity[product]=(dotproducts[product]/(docs_norm[product]*query_norm))
        cosine_sorted=[]

        for key, value in sorted(cosine_similarity.items(), key=lambda item: (item[1],item[0]),reverse=True):
            cosine_sorted.append(key)
        cosine_sorted=cosine_sorted[:k]

        results=[]

        for file in cosine_sorted:
            opentsv=open("doc_tsv/"+file+".tsv","r",encoding="utf8")
            lines=opentsv.readlines()

            for x in lines:
                results.append([x.split('\t')[7],x.split('\t')[4],x.split('\t')[2],x.split('\t')[8],cosine_similarity[file]])
            opentsv.close()

        result=pd.DataFrame(results,columns=['Title','Description','City','URL','Similarity'])
        result.Title = result.Title.str.replace('$', '$\$$') #escape the problem with latex codification
        result.Description = result.Description.str.replace('$', '$\$$') #escape the problem with latex codification

    result.style.set_properties(*{'text-align': 'center'})
    
    return result.style.format({'URL': make_clickable})

In [514]:
searchEngine_2()

Insert your query: garden house dog
How many results do you want to see? 4


In [515]:
searchEngine_2()

Insert your query: dog cat
How many results do you want to see? 3


In [516]:
searchEngine_2()

Insert your query: snd
How many results do you want to see? 6
there are no results that match your search criteria: snd


# 4. Define a new score!

In [517]:
import numpy as np

In [518]:
df["price"] = df["average_rate_per_night"].replace({'\$':''}, regex = True)
df["price"] = df["price"].replace(np.nan, '0', regex=True)

In [520]:
df.price = df.price.astype("int") #make the price as int


In [522]:
df["bedroom"] = df["bedrooms_count"].replace({'Studio':'1'}, regex=True)
df["bedroom"] = df["bedroom"].replace(np.nan, '0', regex=True)
df.bedroom = df.bedroom.astype("int")

In [523]:
df["price_score"] = abs((df["price"] - df["price"].max() )/(df["price"].max() - df["price"].min()) )
df["bed_score"] = (df["bedroom"] - df["bedroom"].min() )/(df["bedroom"].max() - df["bedroom"].min())

In [524]:
df["av_score"] = (df["price_score"] + df["bed_score"])/2

In [525]:
av_price_city = df.groupby("city")["price"].agg(['mean','count','max','min'])

In [526]:
av_price_city["min_int"] = (av_price_city["mean"] - av_price_city["min"])/3
av_price_city["max_int"] = (av_price_city["max"] - av_price_city["mean"])/3

In [527]:
newdf = pd.merge(df, av_price_city, on="city")

In [528]:
def city_score(df):
    if df['price'] < df['min'] + df['min_int']:
        return 5
    elif df['price'] < df['min'] + 2*df['min_int']:
        return 4 
    elif df['price'] < df['mean'] + df['max_int']:
        return 3
    elif df['price'] < df['mean'] + 2*df['max_int']:
        return 2
    else:
        return 1

newdf['city_score'] = newdf.apply(city_score, axis=1)

In [529]:
newdf["city_score"] = (newdf["city_score"] - newdf["city_score"].min() )/(newdf["city_score"].max() - newdf["city_score"].min())

In [530]:
newdf.loc[newdf['count'] < 5, 'city_score'] = 0.5 

In [531]:
newdf=newdf.drop(['mean','count','max','min','min_int','max_int', "av_score"],axis=1)

In [532]:
newdf.head()

Unnamed: 0 average_rate_per_night bedrooms_count    city date_of_listing  \
0           1                    $27              2  Humble        May 2016   
1          54                   $100              2  Humble    January 2016   
2          56                    $81              3  Humble    January 2017   
3          92                   $200              4  Humble   November 2014   
4         135                   $175              3  Humble   February 2016   

                                         description   latitude  longitude  \
0  [welcom, stay, privat, room, queen, bed, detac...  30.020138 -95.293996   
1  [My, home, built, 2016, 5, min, airport, quiet...  30.019380 -95.308188   
2  [entir, 3, bedroom, 2, full, bath, home, quiet...  30.000943 -95.258168   
3  [4, bedroom, 1, live, room, 1, studi, room, 3,...  29.929538 -95.250962   
4  [3, bedroom, 2, 5, bathroom, custom, builder, ...  29.986569 -95.228184   

                                               title  \
0   [2, privat, room, bathroom, 10min, iah, airport]   
1                  [cozi, second, floor, minut, iah]   
2  [entir, home, 5, mile, from, iah, block, hwi, ...   
3             [2, stori, home, bush, int'l, airport]   
4  [singl, stori, golf, cours, home, 15, minut, iah]   

                                                 url  price  bedroom  \
0  https://www.airbnb.com/rooms/18520444?location...     27        2   
1  https://www.airbnb.com/rooms/16925131?location...    100        2   
2  https://www.airbnb.com/rooms/17006337?location...     81        3   
3  https://www.airbnb.com/rooms/4520039?location=...    200        4   
4  https://www.airbnb.com/rooms/16496167?location...    175        3   

   price_score  bed_score  city_score  
0       0.9973   0.153846        1.00  
1       0.9900   0.153846        1.00  
2       0.9919   0.230769        1.00  
3       0.9800   0.307692        0.75  
4       0.9825   0.230769        0.75

In [533]:
newdf["new_score"] = (newdf["price_score"] + newdf["bed_score"] + newdf["city_score"])/3

In [534]:
newdf.head()

Unnamed: 0 average_rate_per_night bedrooms_count    city date_of_listing  \
0           1                    $27              2  Humble        May 2016   
1          54                   $100              2  Humble    January 2016   
2          56                    $81              3  Humble    January 2017   
3          92                   $200              4  Humble   November 2014   
4         135                   $175              3  Humble   February 2016   

                                         description   latitude  longitude  \
0  [welcom, stay, privat, room, queen, bed, detac...  30.020138 -95.293996   
1  [My, home, built, 2016, 5, min, airport, quiet...  30.019380 -95.308188   
2  [entir, 3, bedroom, 2, full, bath, home, quiet...  30.000943 -95.258168   
3  [4, bedroom, 1, live, room, 1, studi, room, 3,...  29.929538 -95.250962   
4  [3, bedroom, 2, 5, bathroom, custom, builder, ...  29.986569 -95.228184   

                                               title  \
0   [2, privat, room, bathroom, 10min, iah, airport]   
1                  [cozi, second, floor, minut, iah]   
2  [entir, home, 5, mile, from, iah, block, hwi, ...   
3             [2, stori, home, bush, int'l, airport]   
4  [singl, stori, golf, cours, home, 15, minut, iah]   

                                                 url  price  bedroom  \
0  https://www.airbnb.com/rooms/18520444?location...     27        2   
1  https://www.airbnb.com/rooms/16925131?location...    100        2   
2  https://www.airbnb.com/rooms/17006337?location...     81        3   
3  https://www.airbnb.com/rooms/4520039?location=...    200        4   
4  https://www.airbnb.com/rooms/16496167?location...    175        3   

   price_score  bed_score  city_score  new_score  
0       0.9973   0.153846        1.00   0.717049  
1       0.9900   0.153846        1.00   0.714615  
2       0.9919   0.230769        1.00   0.740890  
3       0.9800   0.307692        0.75   0.679231  
4       0.9825   0.230769        0.75   0.654423

In [535]:
scores = pd.DataFrame(columns = ["doc", "av_score"])

In [536]:
scores["doc"] = newdf.index

In [537]:
scores["av_score"]=newdf.new_score

In [540]:
newlist=scores.values.tolist()

In [541]:
scores_dict = {}

for i in newlist:
    scores_dict["doc_"+str(int(i[0]))]=i[1]

In [542]:
scores_dict

{'doc_0': 0.7170487179487179,
 'doc_1': 0.7146153846153847,
 'doc_2': 0.7408897435897437,
 'doc_3': 0.6792307692307693,
 'doc_4': 0.6544230769230769,
 'doc_5': 0.5429487179487179,
 'doc_6': 0.6805641025641025,
 'doc_7': 0.6914076923076923,
 'doc_8': 0.6893410256410256,
 'doc_9': 0.6911076923076923,
 'doc_10': 0.7146153846153847,
 'doc_11': 0.6906410256410256,
 'doc_12': 0.6910076923076923,
 'doc_13': 0.6911410256410256,
 'doc_14': 0.6915076923076923,
 'doc_15': 0.7167153846153846,
 'doc_16': 0.691474358974359,
 'doc_17': 0.6906410256410256,
 'doc_18': 0.6903410256410257,
 'doc_19': 0.6911410256410256,
 'doc_20': 0.6903410256410257,
 'doc_21': 0.5949051282051282,
 'doc_22': 0.6910076923076923,
 'doc_23': 0.691474358974359,
 'doc_24': 0.6911410256410256,
 'doc_25': 0.6891743589743591,
 'doc_26': 0.5692307692307693,
 'doc_27': 0.5346153846153846,
 'doc_28': 0.715948717948718,
 'doc_29': 0.5173076923076924,
 'doc_30': 0.739523076923077,
 'doc_31': 0.7669974358974359,
 'doc_32': 0.567589743

In [544]:
with open("scores_dict.json", "w", encoding = "utf8") as myfile:
    myfile.write(json.dumps(scores_dict))

In [632]:
#Search Engine 3

def searchEngine_3():
    query = input("Insert your query: ") #user input
    
    filters = list(input("please enter the filters you want separated by space or leave blank:\ntype\n1 for city\n2 for bedrooms\n3 for price\n").split())
                
    

    query = clean(query) #tokenizing, stemming, removing stop words and punctuation
    
    inverted_index = json.loads(open("/Users/milpro/Desktop/Universita/ADM_Aris/HW3/inverted_index.json").read())


    for i in set(query):
        if i in vocabulary:
            query.remove(i)
            query.append(vocabulary[i])
        else:
            query.remove(i)
    
    docs = []
    query = set(query)
    
    try:
        for i in query:
            docs.append(set(inverted_index[i]))

    
        docs = set.intersection(*docs)

    except: #make a print of exception "result for your query doesn't exist"

        return print("Result for your query doesn't exist.") #it stops the function if there aren't match 

    results = []
    
    
    
    for file in docs:
        opentsv = open("doc_tsv/" + file + ".tsv", "r", encoding="utf8")
        lines = opentsv.readlines()
        for x in lines:
            results.append([x.split('\t')[7], x.split('\t')[4], x.split('\t')[2],
                            int(x.split("\t")[0].replace("$", "")), int(x.split("\t")[1].replace("Studio", "1")),
                            x.split('\t')[8], scores_dict[file]])
        opentsv.close()
    

    result = pd.DataFrame(results, columns = ['Title', 'Description', 'City', "Price", "Bedroom", 'URL', "Score"])
    result.Title = result.Title.str.replace('$', '$\$$') #escape the problem with latex codification
    result.Description = result.Description.str.replace('$', '$\$$') #escape the problem with latex codification
    
    result = result.sort_values(by=['Score'], ascending=False)
    result = result.reset_index(drop=True)
    result.index += 1
    
    result.style.set_properties(*{'text-align': 'center'})
    
    if filters != []:
        #filters = map(int,filters)
        if "1" in filters :
            city = input("Type the name of a city: ")
            result = result[result.City==city]
            
        if "2" in filters :
            min_bed,max_bed = list(map(int,input("Type the minimun and maximum number of bedroom separeted by space: ").split()))
            result = result[result.Bedroom <= max_bed]
            result = result[result.Bedroom >= min_bed ]
        if "3" in filters :
            min_price, max_price = list(map(int,input("Type the minimun and maximum price separeted by space: ").split()))
            result = result[result.Price <= max_price ]
            result = result[result.Price >= min_price ]
        result = result.reset_index(drop=True)
        result.index += 1
    idx=0
    result.insert(idx, "Ranking", result.index)
    
    result = result.drop(["Price", "Bedroom", "Score"],axis=1)
    
    return result.style.format({'URL': make_clickable}) #make_clickable function
   


In [633]:
searchEngine_3()

Insert your query: pergola
please enter the filters you want separated by space or leave blank:
type
1 for city
2 for bedrooms
3 for price

